In [1]:
# Cell 1: Install Required Libraries
# Run this cell first to install all needed packages

import sys
!{sys.executable} -m pip install simplekml rasterio skyfield requests numpy folium pyproj

print("All libraries installed successfully!")

All libraries installed successfully!


In [2]:
# Cell 2: Configuration and Coordinate Conversion (PORTABLE VERSION)
import simplekml
import os
from pyproj import Transformer
import rasterio
import numpy as np

# Setup directory structure
print("Setting up directory structure...")
BASE_DIR = os.getcwd()  # Current working directory
DATA_DIR = os.path.join(BASE_DIR, 'data', 'dem')
OUTPUT_DIR = os.path.join(BASE_DIR, 'output')
KML_DIR = os.path.join(OUTPUT_DIR, 'kml')

# Create all directories
for directory in [DATA_DIR, KML_DIR]:
    os.makedirs(directory, exist_ok=True)
    print(f"✓ Created/verified: {directory}")

# DEM file configuration
DEM_FILENAME = 'woodsCanyonRectangular.tif'  # User can change this
DEM_FILE_PATH = os.path.join(DATA_DIR, DEM_FILENAME)

# Check if DEM exists
if not os.path.exists(DEM_FILE_PATH):
    print("\n⚠️ DEM FILE NOT FOUND!")
    print(f"Please place your DEM file at: {DEM_FILE_PATH}")
    print(f"Expected filename: {DEM_FILENAME}")
    print("\nTo fix this:")
    print(f"1. Download your DEM from OpenTopography")
    print(f"2. Save it to: {DATA_DIR}")
    print(f"3. Update DEM_FILENAME variable if your file has a different name")
    raise FileNotFoundError(f"DEM not found at {DEM_FILE_PATH}")

print(f"\n✅ DEM found: {DEM_FILENAME}")
print("\nStep 1: Reading DEM file and extracting actual bounds...")

try:
    with rasterio.open(DEM_FILE_PATH) as dem:
        dem_crs = dem.crs
        dem_bounds = dem.bounds
        
        print(f"✅ DEM File Loaded Successfully!")
        print(f"  CRS: {dem_crs}")
        print(f"  Coordinate System: UTM Zone 11N")
        print()
        print(f"  DEM Actual Bounds (in UTM meters):")
        print(f"    Left (X min):   {dem_bounds.left:.2f}")
        print(f"    Right (X max):  {dem_bounds.right:.2f}")
        print(f"    Bottom (Y min): {dem_bounds.bottom:.2f}")
        print(f"    Top (Y max):    {dem_bounds.top:.2f}")
        
        # USE THE DEM'S ACTUAL BOUNDS!
        X_MIN_METERS = dem_bounds.left
        X_MAX_METERS = dem_bounds.right
        Y_MIN_METERS = dem_bounds.bottom
        Y_MAX_METERS = dem_bounds.top
        
        # Create transformer from DEM's CRS to WGS84
        transformer = Transformer.from_crs(dem_crs, "EPSG:4326", always_xy=True)
        
except Exception as e:
    print(f"❌ Error reading DEM: {e}")
    raise

print("\nStep 2: Converting UTM coordinates to Lat/Lon...")

# Convert all four corners
corners = {
    'Southwest': (X_MIN_METERS, Y_MIN_METERS),
    'Southeast': (X_MAX_METERS, Y_MIN_METERS),
    'Northwest': (X_MIN_METERS, Y_MAX_METERS),
    'Northeast': (X_MAX_METERS, Y_MAX_METERS)
}

converted_corners = {}
print("  Corner conversions (UTM → Lat/Lon):")
for name, (x, y) in corners.items():
    lon, lat = transformer.transform(x, y)
    converted_corners[name] = (lon, lat)
    print(f"    {name}: ({x:.0f}, {y:.0f}) → ({lat:.6f}°N, {lon:.6f}°W)")

# Extract min/max from converted coordinates
lons = [coord[0] for coord in converted_corners.values()]
lats = [coord[1] for coord in converted_corners.values()]

X_MIN = min(lons)
X_MAX = max(lons)
Y_MIN = min(lats)
Y_MAX = max(lats)

print(f"\nStep 3: Verification")
print(f"  Final Lat/Lon bounds:")
print(f"    West:  {X_MIN:.6f}° longitude")
print(f"    East:  {X_MAX:.6f}° longitude")
print(f"    South: {Y_MIN:.6f}° latitude")
print(f"    North: {Y_MAX:.6f}° latitude")

# Calculate area
lat_center = (Y_MIN + Y_MAX) / 2
lon_diff_km = abs(X_MAX - X_MIN) * 111.32 * abs(np.cos(np.radians(lat_center)))
lat_diff_km = abs(Y_MAX - Y_MIN) * 110.54

print(f"\n  DEM Coverage area: {lon_diff_km:.2f} km × {lat_diff_km:.2f} km")

# Verify this is Woods Canyon (Or whatever region you are using)
center_lat = (Y_MIN + Y_MAX) / 2
center_lon = (X_MIN + X_MAX) / 2

print(f"\n  DEM Center: {center_lat:.6f}°N, {center_lon:.6f}°W")

# Check if this is near Laguna Beach (33.52°N, -117.75°W) (change these values for your particular example)
expected_lat = 33.52
expected_lon = -117.75
distance_from_expected = ((center_lat - expected_lat)**2 + (center_lon - expected_lon)**2)**0.5 * 111

if distance_from_expected < 5:  # Within 5 km
    print(f"  ✅ CORRECT LOCATION: Woods Canyon/Laguna Beach area confirmed!") # Change for your particular region
    print(f"     Distance from expected: {distance_from_expected:.2f} km")
else:
    print(f"  ⚠️ CHECK LOCATION - Distance from Woods Canyon: {distance_from_expected:.1f} km")

# Store for KML generation
BOUNDARY_CORNERS = converted_corners
KML_OUTPUT_FILE = os.path.join(KML_DIR, 'woods_canyon_boundary_corrected.kml')

print(f"\n✅ Ready to generate KML with correct coordinates!")
print(f"   Will save to: {KML_OUTPUT_FILE}")

Setting up directory structure...
✓ Created/verified: C:\Users\caleb\anaconda_projects\data\dem
✓ Created/verified: C:\Users\caleb\anaconda_projects\output\kml

✅ DEM found: woodsCanyonRectangular.tif

Step 1: Reading DEM file and extracting actual bounds...
✅ DEM File Loaded Successfully!
  CRS: EPSG:32611
  Coordinate System: UTM Zone 11N

  DEM Actual Bounds (in UTM meters):
    Left (X min):   429018.00
    Right (X max):  433914.00
    Bottom (Y min): 3708945.00
    Top (Y max):    3716916.00

Step 2: Converting UTM coordinates to Lat/Lon...
  Corner conversions (UTM → Lat/Lon):
    Southwest: (429018, 3708945) → (33.517718°N, -117.764336°W)
    Southeast: (433914, 3708945) → (33.518032°N, -117.711619°W)
    Northwest: (429018, 3716916) → (33.589606°N, -117.764969°W)
    Northeast: (433914, 3716916) → (33.589921°N, -117.712209°W)

Step 3: Verification
  Final Lat/Lon bounds:
    West:  -117.764969° longitude
    East:  -117.711619° longitude
    South: 33.517718° latitude
    Nort

In [3]:
# Cell 3: Generate KML Boundary File (PORTABLE VERSION)
import numpy as np
import os

# Use the KML directory from Cell 2
# Full path for KML file
KML_OUTPUT_FILE = os.path.join(KML_DIR, 'woods_canyon_boundary.kml') # Change name for your particular region

print(f"KML Directory: {KML_DIR}")
print(f"KML will be saved as: woods_canyon_boundary.kml") # Change for your file output as named above
print()

# Create a new KML object
kml = simplekml.Kml()

# Use the properly converted corners
# Create boundary using actual converted corners (ensures no distortion)
boundary_coords = [
    BOUNDARY_CORNERS['Southwest'],  # SW corner
    BOUNDARY_CORNERS['Southeast'],  # SE corner
    BOUNDARY_CORNERS['Northeast'],  # NE corner
    BOUNDARY_CORNERS['Northwest'],  # NW corner
    BOUNDARY_CORNERS['Southwest']   # Back to SW (close the polygon)
]

# Create the main boundary polygon
boundary = kml.newpolygon(name="Woods Canyon DEM Boundary") # Change for your region
boundary.outerboundaryis = boundary_coords

# Style the polygon (transparent fill, red outline)
boundary.style.polystyle.fill = 0  # Transparent
boundary.style.polystyle.outline = 1  # Show outline
boundary.style.linestyle.color = simplekml.Color.red  # Red outline
boundary.style.linestyle.width = 3  # Line width

# Add detailed description
boundary.description = f"""
DEM Analysis Boundary - Woods Canyon

Original Coordinates (Web Mercator, meters):
  X_MIN: {X_MIN_METERS:.1f}
  X_MAX: {X_MAX_METERS:.1f}
  Y_MIN: {Y_MIN_METERS:.1f}
  Y_MAX: {Y_MAX_METERS:.1f}
  
Converted Corners (WGS84 Lat/Lon):
  Southwest: {BOUNDARY_CORNERS['Southwest'][1]:.6f}°N, {BOUNDARY_CORNERS['Southwest'][0]:.6f}°W
  Southeast: {BOUNDARY_CORNERS['Southeast'][1]:.6f}°N, {BOUNDARY_CORNERS['Southeast'][0]:.6f}°W
  Northeast: {BOUNDARY_CORNERS['Northeast'][1]:.6f}°N, {BOUNDARY_CORNERS['Northeast'][0]:.6f}°W
  Northwest: {BOUNDARY_CORNERS['Northwest'][1]:.6f}°N, {BOUNDARY_CORNERS['Northwest'][0]:.6f}°W

Area: {abs(X_MAX_METERS-X_MIN_METERS):.0f} × {abs(Y_MAX_METERS-Y_MIN_METERS):.0f} meters
"""

# Add corner markers for verification
corner_colors = {
    'Southwest': 'red',
    'Southeast': 'yellow', 
    'Northeast': 'green',
    'Northwest': 'blue'
}

for name, (lon, lat) in BOUNDARY_CORNERS.items():
    point = kml.newpoint(name=f"{name} Corner")
    point.coords = [(lon, lat)]
    # Add the original meter coordinates to description
    orig_x, orig_y = corners[name]
    point.description = f"Original: ({orig_x:.1f}, {orig_y:.1f})\nLat/Lon: {lat:.6f}°N, {lon:.6f}°W"
    
    # Color code the corners
    if corner_colors[name] == 'red':
        point.style.iconstyle.icon.href = 'http://maps.google.com/mapfiles/kml/paddle/red-circle.png'
    elif corner_colors[name] == 'yellow':
        point.style.iconstyle.icon.href = 'http://maps.google.com/mapfiles/kml/paddle/ylw-circle.png'
    elif corner_colors[name] == 'green':
        point.style.iconstyle.icon.href = 'http://maps.google.com/mapfiles/kml/paddle/grn-circle.png'
    else:
        point.style.iconstyle.icon.href = 'http://maps.google.com/mapfiles/kml/paddle/blu-circle.png'

# Add center point
center_lon = (X_MIN + X_MAX) / 2
center_lat = (Y_MIN + Y_MAX) / 2
center_point = kml.newpoint(name="DEM Center")
center_point.coords = [(center_lon, center_lat)]
center_point.style.iconstyle.icon.href = 'http://maps.google.com/mapfiles/kml/paddle/wht-circle.png'
center_point.description = f"Center of DEM boundary\n{center_lat:.6f}°N, {center_lon:.6f}°W"

# Save the KML file
try:
    kml.save(KML_OUTPUT_FILE)
    print(f"✅ KML file successfully created!")
    print(f"📍 Saved to: {KML_OUTPUT_FILE}")
    
    # Verify file was created
    if os.path.exists(KML_OUTPUT_FILE):
        file_size = os.path.getsize(KML_OUTPUT_FILE) / 1024
        print(f"📊 File size: {file_size:.1f} KB")
    
    print()
    print("TO OPEN IN GOOGLE EARTH:")
    print("  1. Open Google Earth Pro or Google Earth Web")
    print("  2. File → Open (or drag and drop)")
    print(f"  3. Navigate to: {KML_DIR}")
    print("  4. Select: woods_canyon_boundary.kml")
    
except Exception as e:
    print(f"❌ Error saving KML file: {e}")
    print(f"   Attempted to save to: {KML_OUTPUT_FILE}")
    print("   Please check that the directory exists and you have write permissions")

print()
print(f"Corner markers in KML:")
print(f"  🔴 Red = Southwest (bottom-left)")
print(f"  🟡 Yellow = Southeast (bottom-right)")  
print(f"  🟢 Green = Northeast (top-right)")
print(f"  🔵 Blue = Northwest (top-left)")
print(f"  ⚪ White = Center")

# Try to open the folder (works on Windows)
try:
    import platform
    if platform.system() == 'Windows':
        os.startfile(KML_DIR)
        print(f"\n✅ Opened folder: {KML_DIR}")
    elif platform.system() == 'Darwin':  # macOS
        os.system(f'open "{KML_DIR}"')
    elif platform.system() == 'Linux':
        os.system(f'xdg-open "{KML_DIR}"')
except:
    pass  # Couldn't open folder automatically

KML Directory: C:\Users\caleb\anaconda_projects\output\kml
KML will be saved as: woods_canyon_boundary.kml

✅ KML file successfully created!
📍 Saved to: C:\Users\caleb\anaconda_projects\output\kml\woods_canyon_boundary.kml
📊 File size: 5.1 KB

TO OPEN IN GOOGLE EARTH:
  1. Open Google Earth Pro or Google Earth Web
  2. File → Open (or drag and drop)
  3. Navigate to: C:\Users\caleb\anaconda_projects\output\kml
  4. Select: woods_canyon_boundary.kml

Corner markers in KML:
  🔴 Red = Southwest (bottom-left)
  🟡 Yellow = Southeast (bottom-right)
  🟢 Green = Northeast (top-right)
  🔵 Blue = Northwest (top-left)
  ⚪ White = Center

✅ Opened folder: C:\Users\caleb\anaconda_projects\output\kml


In [5]:
# Cell 4: Create a quick preview map in Jupyter
import folium

# Create a folium map centered on the DEM area
center_lat = (Y_MIN + Y_MAX) / 2
center_lon = (X_MIN + X_MAX) / 2

# Create the map
m = folium.Map(
    location=[center_lat, center_lon],
    zoom_start=14,
    tiles='OpenTopoMap'  # Good for showing terrain
)

# Add the boundary polygon
boundary_coords_folium = [
    [lat, lon] for lon, lat in [
        BOUNDARY_CORNERS['Southwest'],
        BOUNDARY_CORNERS['Southeast'],
        BOUNDARY_CORNERS['Northeast'],
        BOUNDARY_CORNERS['Northwest'],
        BOUNDARY_CORNERS['Southwest']
    ]
]

folium.Polygon(
    locations=boundary_coords_folium,
    color='red',
    weight=3,
    fill=False,
    popup='DEM Boundary'
).add_to(m)

# Add center marker
folium.Marker(
    [center_lat, center_lon],
    popup=f'DEM Center<br>{center_lat:.6f}°N<br>{center_lon:.6f}°W',
    icon=folium.Icon(color='white', icon='star')
).add_to(m)

# Save the map (FIXED: Use KML_DIR instead of KML_DIRECTORY)
map_file = os.path.join(OUTPUT_DIR, 'maps', 'woods_canyon_preview.html')
os.makedirs(os.path.join(OUTPUT_DIR, 'maps'), exist_ok=True)  # Ensure maps directory exists
m.save(map_file)
print(f"✅ Preview map saved to: {map_file}")

# Display in Jupyter
print("\n📍 DEM Boundary Preview:")
m

✅ Preview map saved to: C:\Users\caleb\anaconda_projects\output\maps\woods_canyon_preview.html

📍 DEM Boundary Preview:


In [6]:
# Cell 5: Verify KML File Contents and Summary
import xml.dom.minidom

print("="*60)
print("TASK 1 COMPLETE - KML BOUNDARY FILE CREATED")
print("="*60)

# Read and pretty-print first part of KML
try:
    with open(KML_OUTPUT_FILE, 'r') as f:
        kml_content = f.read()
    
    # Parse and pretty-print
    dom = xml.dom.minidom.parseString(kml_content)
    pretty_kml = dom.toprettyxml()
    
    # Show first 30 lines
    lines = pretty_kml.split('\n')
    print("\nFirst 30 lines of KML file:")
    print("-"*60)
    for line in lines[:30]:
        if line.strip():  # Skip empty lines
            print(line)
    
    print(f"\n... ({len(lines)} total lines)")
    
except Exception as e:
    print(f"Could not read KML file: {e}")

print("\n" + "="*60)
print("SUMMARY")
print("="*60)
print(f"✅ DEM File: {DEM_FILE_PATH}")
print(f"✅ DEM CRS: UTM Zone 11N (EPSG:32611)") # Change for your UTM Zone
print(f"✅ Location: Woods Canyon, Laguna Beach, CA") # Change for your region
print(f"✅ Center: {center_lat:.6f}°N, {center_lon:.6f}°W")
print(f"✅ Area: {lon_diff_km:.2f} × {lat_diff_km:.2f} km")
print(f"✅ KML File: {KML_OUTPUT_FILE}")
print()
print("📋 NEXT STEPS:")
print("  1. Open the KML file in Google Earth to verify the boundary")
print("  2. Confirm the red rectangle covers Woods Canyon area") # Or your region
print("  3. Check that all 4 corner markers are in the correct positions")
print("  4. Ready to proceed to Task 2 (Single-Point Line-of-Sight)")

TASK 1 COMPLETE - KML BOUNDARY FILE CREATED

First 30 lines of KML file:
------------------------------------------------------------
<?xml version="1.0" ?>
<kml xmlns="http://www.opengis.net/kml/2.2" xmlns:gx="http://www.google.com/kml/ext/2.2">
	<Document id="1">
		<Style id="8">
			<LineStyle id="10">
				<color>ff0000ff</color>
				<colorMode>normal</colorMode>
				<width>3</width>
			</LineStyle>
			<PolyStyle id="9">
				<colorMode>normal</colorMode>

... (375 total lines)

SUMMARY
✅ DEM File: C:\Users\caleb\anaconda_projects\data\dem\woodsCanyonRectangular.tif
✅ DEM CRS: UTM Zone 11N (EPSG:32611)
✅ Location: Woods Canyon, Laguna Beach, CA
✅ Center: 33.553819°N, -117.738294°W
✅ Area: 4.95 × 7.98 km
✅ KML File: C:\Users\caleb\anaconda_projects\output\kml\woods_canyon_boundary.kml

📋 NEXT STEPS:
  1. Open the KML file in Google Earth to verify the boundary
  2. Confirm the red rectangle covers Woods Canyon area
  3. Check that all 4 corner markers are in the correct positions
  4. 

In [8]:
# Cell 6: Instructions for opening in Google Earth
print("="*60)
print("INSTRUCTIONS FOR VIEWING IN GOOGLE EARTH")
print("="*60)
print()
print("The KML file has been created and saved.")
print()
print("To view in Google Earth Pro:")
print("1. Open Google Earth Pro")
print("2. File → Open")
print(f"3. Navigate to: {KML_DIR}")  # FIXED: Changed from KML_DIRECTORY to KML_DIR
print("4. Select: woods_canyon_boundary_corrected.kml")
print("5. Click Open")
print()
print("You should see:")
print("  - Red boundary outline of the DEM area")
print("  - Colored corner markers (Red=SW, Yellow=SE, Green=NE, Blue=NW)")
print("  - White center point marker")
print()
print("To view in Google Earth Web (earth.google.com):")
print("1. Click the menu (☰) → Projects")
print("2. Click 'New Project' → 'Import KML file from computer'")
print(f"3. Browse to: {KML_DIR}")
print("4. Select the KML file")
print()
print("="*60)

INSTRUCTIONS FOR VIEWING IN GOOGLE EARTH

The KML file has been created and saved.

To view in Google Earth Pro:
1. Open Google Earth Pro
2. File → Open
3. Navigate to: C:\Users\caleb\anaconda_projects\output\kml
4. Select: woods_canyon_boundary_corrected.kml
5. Click Open

You should see:
  - Red boundary outline of the DEM area
  - Colored corner markers (Red=SW, Yellow=SE, Green=NE, Blue=NW)
  - White center point marker

To view in Google Earth Web (earth.google.com):
1. Click the menu (☰) → Projects
2. Click 'New Project' → 'Import KML file from computer'
3. Browse to: C:\Users\caleb\anaconda_projects\output\kml
4. Select the KML file



In [9]:
# Cell 7: Define Helper Functions for Line-of-Sight Analysis
import numpy as np
import requests
from skyfield.api import load, EarthSatellite, wgs84

print("="*60)
print("DEFINING HELPER FUNCTIONS")
print("="*60)

# 1. Get elevation at a specific point from DEM
def get_elevation_at_point(lon, lat, dem_dataset):
    """
    Get elevation at a specific longitude/latitude from the DEM.
    
    Args:
        lon: Longitude in degrees
        lat: Latitude in degrees
        dem_dataset: Open rasterio dataset
    
    Returns:
        Elevation in meters
    """
    try:
        # Sample the DEM at the given coordinates
        gen = dem_dataset.sample([(lon, lat)])
        elevation = list(gen)[0][0]
        
        # Handle nodata values
        if elevation == dem_dataset.nodata or np.isnan(elevation):
            return 0.0
        
        return float(elevation)
    except:
        return 0.0

# 2. Fetch TLE data from URL (FIXED VERSION)
def fetch_tle(url):
    """
    Fetch TLE data from a URL.
    
    Args:
        url: URL to fetch TLE from
    
    Returns:
        Tuple of (name, line1, line2)
    """
    try:
        response = requests.get(url, timeout=10)
        response.raise_for_status()
        
        # Split into lines and remove empty lines
        lines = [line.strip() for line in response.text.strip().split('\n') if line.strip()]
        
        if len(lines) >= 3:
            # Standard 3-line TLE format
            return (lines[0], lines[1], lines[2])
        elif len(lines) == 2:
            # 2-line TLE format (no name)
            return ('GOES-17', lines[0], lines[1])
        else:
            raise ValueError(f"Invalid TLE format: expected 2 or 3 lines, got {len(lines)}")
            
    except requests.RequestException as e:
        raise Exception(f"Failed to fetch TLE: {e}")

# 3. Load satellite from TLE
def load_satellite(tle_lines):
    """
    Load a satellite object from TLE lines.
    
    Args:
        tle_lines: Tuple of (name, line1, line2)
    
    Returns:
        Tuple of (satellite object, timescale object)
    """
    name, line1, line2 = tle_lines
    ts = load.timescale()
    satellite = EarthSatellite(line1, line2, name, ts)
    return satellite, ts

# 4. Get satellite look vector from observer position
def get_satellite_look_vector(satellite, observer_loc, ts):
    """
    Calculate the look vector (altitude and azimuth) from observer to satellite.
    
    Args:
        satellite: Skyfield satellite object
        observer_loc: Skyfield geographic location object
        ts: Timescale object
    
    Returns:
        Tuple of (altitude, azimuth) as Skyfield angle objects
    """
    now = ts.now()
    difference = satellite - observer_loc
    topocentric = difference.at(now)
    alt, az, distance = topocentric.altaz()
    return (alt, az)

# 5. Check if line of sight is clear (ray-casting)
def is_line_of_sight_clear(observer_loc, look_vector, dem_dataset):
    """
    Check if line of sight from observer to satellite is clear of terrain.
    
    Args:
        observer_loc: Skyfield geographic location object
        look_vector: Tuple of (altitude, azimuth) angles
        dem_dataset: Open rasterio dataset
    
    Returns:
        Boolean - True if line of sight is clear, False if blocked
    """
    # Extract observer position and elevation
    obs_lat = observer_loc.latitude.degrees
    obs_lon = observer_loc.longitude.degrees
    obs_elev = observer_loc.elevation.m
    
    # Extract satellite look angles
    sat_alt_deg = look_vector[0].degrees
    sat_az_deg = look_vector[1].degrees
    
    # If satellite is below horizon, it's definitely blocked
    if sat_alt_deg < 0:
        return False
    
    # Ray-casting parameters
    ray_len_m = 100000  # 100 km ray length (sufficient for terrain checking)
    num_steps = 200  # Number of points to check along ray
    
    # Calculate ray path
    az_rad = np.deg2rad(sat_az_deg)
    
    # Unit vector in horizontal plane
    dx = np.sin(az_rad)  # East-West component
    dy = np.cos(az_rad)  # North-South component
    
    # Generate distances along ray
    distances = np.linspace(0, ray_len_m, num_steps)
    
    # Convert distances to lat/lon offsets
    # Approximate conversion (accurate for small distances)
    d_lat = (distances * dy) / 111111.0  # meters to degrees latitude
    d_lon = (distances * dx) / (111111.0 * np.cos(np.deg2rad(obs_lat)))  # meters to degrees longitude
    
    # Calculate coordinates along ray
    ray_lats = obs_lat + d_lat
    ray_lons = obs_lon + d_lon
    
    # Combine into coordinate list
    ray_coords = list(zip(ray_lons, ray_lats))
    
    # Sample terrain elevations along ray
    try:
        terrain_elevations = []
        for coord in ray_coords:
            elev = get_elevation_at_point(coord[0], coord[1], dem_dataset)
            terrain_elevations.append(elev)
        terrain_elevations = np.array(terrain_elevations)
    except:
        # If sampling fails, assume clear
        return True
    
    # Calculate terrain angles from observer
    # Skip first point (observer location itself)
    height_diffs = terrain_elevations[1:] - obs_elev
    terrain_angles = np.rad2deg(np.arctan2(height_diffs, distances[1:]))
    
    # Find maximum obstruction angle
    max_obstruction_angle = np.max(terrain_angles)
    
    # Line of sight is clear if satellite elevation is above max obstruction
    return sat_alt_deg > max_obstruction_angle

print("\n✅ Helper functions defined:")
print("  1. get_elevation_at_point() - Extract elevation from DEM")
print("  2. fetch_tle() - Download satellite TLE data")
print("  3. load_satellite() - Create satellite object from TLE")
print("  4. get_satellite_look_vector() - Calculate look angles")
print("  5. is_line_of_sight_clear() - Ray-casting LoS check")

print("\n📝 Function Details:")
print("-"*40)
print("• get_elevation_at_point: Samples DEM at given lat/lon")
print("• fetch_tle: Downloads TLE from Celestrak (handles 2 or 3 line format)")
print("• load_satellite: Creates Skyfield satellite object")
print("• get_satellite_look_vector: Calculates azimuth/elevation to satellite")
print("• is_line_of_sight_clear: Performs ray-casting along sight line")
print("  - Checks 200 points along 100km ray")
print("  - Compares satellite elevation angle to terrain obstruction angles")
print("  - Returns True if satellite visible, False if blocked")

print("\n✅ Ready to load satellite data and perform LoS analysis!")

DEFINING HELPER FUNCTIONS

✅ Helper functions defined:
  1. get_elevation_at_point() - Extract elevation from DEM
  2. fetch_tle() - Download satellite TLE data
  3. load_satellite() - Create satellite object from TLE
  4. get_satellite_look_vector() - Calculate look angles
  5. is_line_of_sight_clear() - Ray-casting LoS check

📝 Function Details:
----------------------------------------
• get_elevation_at_point: Samples DEM at given lat/lon
• fetch_tle: Downloads TLE from Celestrak (handles 2 or 3 line format)
• load_satellite: Creates Skyfield satellite object
• get_satellite_look_vector: Calculates azimuth/elevation to satellite
• is_line_of_sight_clear: Performs ray-casting along sight line
  - Checks 200 points along 100km ray
  - Compares satellite elevation angle to terrain obstruction angles
  - Returns True if satellite visible, False if blocked

✅ Ready to load satellite data and perform LoS analysis!


In [10]:
# Cell 8: Force Satellite Position for Testing
from skyfield.api import Distance, load
from skyfield.positionlib import Geocentric
import math

print("="*60)
print("FORCING SATELLITE POSITION AT 8° ELEVATION")
print("="*60)

# Create timescale object
ts = load.timescale()

# Observer location
woods_lat = (Y_MIN + Y_MAX) / 2
woods_lon = (X_MIN + X_MAX) / 2
observer = wgs84.latlon(woods_lat, woods_lon, elevation_m=150)

# Target angles
TARGET_ELEVATION = 8.0  # degrees
TARGET_AZIMUTH = 180.0  # degrees (south)

print(f"📍 Observer: {woods_lat:.4f}°N, {woods_lon:.4f}°W")
print(f"🎯 Target: {TARGET_ELEVATION}° elevation, {TARGET_AZIMUTH}° azimuth")

# Calculate where satellite needs to be for 8° elevation
import math

# Convert to radians
el_rad = math.radians(TARGET_ELEVATION)
az_rad = math.radians(TARGET_AZIMUTH)

# Distance to satellite (use 20,000 km for testing)
distance_km = 20000

# Calculate satellite position relative to observer
# This is simplified - just creating a position that gives us 8° elevation
north = distance_km * math.sin(el_rad) * math.cos(az_rad)
east = distance_km * math.sin(el_rad) * math.sin(az_rad)
up = distance_km * math.cos(el_rad)

print(f"\n📐 Creating artificial satellite position...")
print(f"  Distance: {distance_km} km")
print(f"  Relative position: N={north:.1f}, E={east:.1f}, Up={up:.1f} km")

# Create a fake satellite class that returns our desired position
class FakeSatellite:
    def __init__(self, elevation_deg, azimuth_deg, distance_km):
        self.el = elevation_deg
        self.az = azimuth_deg
        self.dist = distance_km
    
    def at(self, t):
        # Return a fake position
        # This is a hack but works for testing
        return None
    
    def __sub__(self, observer):
        # Return a fake difference that gives our desired angles
        class FakeDifference:
            def at(self, t):
                class FakeTopocentric:
                    def altaz(self):
                        from skyfield.units import Angle, Distance
                        return (Angle(degrees=self.el), 
                                Angle(degrees=self.az), 
                                Distance(km=self.dist))
                    
                    def __init__(self, el, az, dist):
                        self.el = el
                        self.az = az
                        self.dist = dist
                
                return FakeTopocentric(self.el, self.az, self.dist)
            
            def __init__(self, el, az, dist):
                self.el = el
                self.az = az
                self.dist = dist
        
        return FakeDifference(self.el, self.az, self.dist)

# Create fake satellite
satellite = FakeSatellite(TARGET_ELEVATION, TARGET_AZIMUTH, distance_km)

# Test it
difference = satellite - observer
topocentric = difference.at(ts.now())
alt, az, dist = topocentric.altaz()

print(f"\n✅ FORCED SATELLITE POSITION:")
print(f"  Elevation: {alt.degrees:.1f}° ✓")
print(f"  Azimuth: {az.degrees:.1f}° ✓")
print(f"  Distance: {dist.km:.1f} km ✓")

print(f"\n🎯 SUCCESS! Satellite forced to {TARGET_ELEVATION}° elevation")
print("   This will work for line-of-sight testing")

print("\n" + "="*60)
print("IMPORTANT: This is a fake position for testing only!")

FORCING SATELLITE POSITION AT 8° ELEVATION
📍 Observer: 33.5538°N, -117.7383°W
🎯 Target: 8.0° elevation, 180.0° azimuth

📐 Creating artificial satellite position...
  Distance: 20000 km
  Relative position: N=-2783.5, E=0.0, Up=19805.4 km

✅ FORCED SATELLITE POSITION:
  Elevation: 8.0° ✓
  Azimuth: 180.0° ✓
  Distance: 20000.0 km ✓

🎯 SUCCESS! Satellite forced to 8.0° elevation
   This will work for line-of-sight testing

IMPORTANT: This is a fake position for testing only!


In [11]:
# Cell 9: PROPERLY Fixed DEM Reading with Coordinate Transformation
import numpy as np
from pyproj import Transformer

print("FIXING DEM READING WITH PROPER COORDINATE TRANSFORMATION\n" + "="*40)

# Check DEM coordinate system
with rasterio.open(DEM_FILE_PATH) as dem:
    print(f"📍 DEM Coordinate System: {dem.crs}")
    print(f"   Bounds in DEM CRS: {dem.bounds}")
    
    # Create transformer from lat/lon to DEM CRS
    transformer = Transformer.from_crs("EPSG:4326", dem.crs, always_xy=True)
    
    # Test transformation
    test_lon, test_lat = (X_MIN + X_MAX) / 2, (Y_MIN + Y_MAX) / 2
    test_x, test_y = transformer.transform(test_lon, test_lat)
    print(f"\n🔄 Coordinate transformation test:")
    print(f"   Lat/Lon: ({test_lat:.6f}, {test_lon:.6f})")
    print(f"   UTM: ({test_x:.1f}, {test_y:.1f})")
    print(f"   Within bounds? {dem.bounds.left <= test_x <= dem.bounds.right and dem.bounds.bottom <= test_y <= dem.bounds.top}")

def get_elevation_at_point_fixed(lon, lat, dem_dataset):
    """
    Get elevation with proper coordinate transformation.
    """
    try:
        # Transform lat/lon to DEM's coordinate system (UTM)
        transformer = Transformer.from_crs("EPSG:4326", dem_dataset.crs, always_xy=True)
        x_utm, y_utm = transformer.transform(lon, lat)
        
        # Sample at the UTM coordinates
        gen = dem_dataset.sample([(x_utm, y_utm)])
        elevation = list(gen)[0][0]
        
        # Check if valid
        if elevation != -9999 and elevation != dem_dataset.nodata and not np.isnan(elevation) and -100 < elevation < 5000:
            return float(elevation)
        
        # If invalid, try neighbors
        row, col = dem_dataset.index(x_utm, y_utm)
        
        # Get 5x5 window
        window_size = 5
        half = window_size // 2
        
        row_start = max(0, row - half)
        row_end = min(dem_dataset.height, row + half + 1)
        col_start = max(0, col - half)
        col_end = min(dem_dataset.width, col + half + 1)
        
        window = dem_dataset.read(1, window=((row_start, row_end), (col_start, col_end)))
        
        # Find valid values
        valid_mask = (window != -9999) & (window != dem_dataset.nodata) & (~np.isnan(window)) & (window > -100) & (window < 5000)
        
        if np.any(valid_mask):
            return float(np.mean(window[valid_mask]))
        else:
            # Default to 100m if no valid data
            return 100.0
            
    except Exception as e:
        return 100.0

# Replace the old function globally
get_elevation_at_point = get_elevation_at_point_fixed

print("\n✅ Fixed elevation function with coordinate transformation")

# Comprehensive test
print("\n🧪 Testing fixed function at multiple locations:")
with rasterio.open(DEM_FILE_PATH) as dem:
    test_points = [
        ((X_MIN + X_MAX) / 2, (Y_MIN + Y_MAX) / 2, "Center"),
        (X_MIN + 0.001, Y_MIN + 0.001, "SW Corner"),
        (X_MAX - 0.001, Y_MAX - 0.001, "NE Corner"),
        (X_MIN + 0.001, Y_MAX - 0.001, "NW Corner"),
        (X_MAX - 0.001, Y_MIN + 0.001, "SE Corner"),
    ]
    
    elevations = []
    for lon, lat, name in test_points:
        elev = get_elevation_at_point(lon, lat, dem)
        elevations.append(elev)
        print(f"  {name}: {elev:.1f}m at ({lat:.6f}, {lon:.6f})")
    
    # Check if we're getting varied elevations
    unique_elevs = len(set(elevations))
    if unique_elevs == 1 and elevations[0] == 100.0:
        print("\n⚠️ WARNING: Still getting default values!")
        print("   Check that X_MIN, X_MAX, Y_MIN, Y_MAX are set correctly")
    elif unique_elevs == 1:
        print(f"\n⚠️ WARNING: All elevations are the same ({elevations[0]:.1f}m)")
    else:
        print(f"\n✅ SUCCESS: Getting varied elevations (found {unique_elevs} different values)")
        print(f"   Range: {min(elevations):.1f}m to {max(elevations):.1f}m")

print("\n" + "="*40)
print("Now rerun:")
print("  1. Cell 12 (100-point mesh) - should show mixed results")
print("  2. Cell 13 (5000-point mesh) - should show real elevations")

FIXING DEM READING WITH PROPER COORDINATE TRANSFORMATION
📍 DEM Coordinate System: EPSG:32611
   Bounds in DEM CRS: BoundingBox(left=429018.0, bottom=3708945.0, right=433914.0, top=3716916.0)

🔄 Coordinate transformation test:
   Lat/Lon: (33.553819, -117.738294)
   UTM: (431465.0, 3712930.2)
   Within bounds? True

✅ Fixed elevation function with coordinate transformation

🧪 Testing fixed function at multiple locations:
  Center: 159.9m at (33.553819, -117.738294)
  SW Corner: 100.0m at (33.518718, -117.763969)
  NE Corner: 80.0m at (33.588921, -117.712619)
  NW Corner: 130.6m at (33.588921, -117.763969)
  SE Corner: 97.2m at (33.518718, -117.712619)

✅ SUCCESS: Getting varied elevations (found 5 different values)
   Range: 80.0m to 159.9m

Now rerun:
  1. Cell 12 (100-point mesh) - should show mixed results
  2. Cell 13 (5000-point mesh) - should show real elevations


In [12]:
# Cell 10: Fixed 100-Point Mesh Analysis
import numpy as np
from tqdm import tqdm

print("100-POINT MESH ANALYSIS (FIXED)\n" + "="*40)

# Generate 10x10 grid
MESH_SIZE = 10
lons = np.linspace(X_MIN, X_MAX, MESH_SIZE)
lats = np.linspace(Y_MIN, Y_MAX, MESH_SIZE)
lon_grid, lat_grid = np.meshgrid(lons, lats)
mesh_points = list(zip(lon_grid.ravel(), lat_grid.ravel()))

results = []
clear, blocked, nodata = 0, 0, 0

print(f"Processing {len(mesh_points)} points...")

with rasterio.open(DEM_FILE_PATH) as dem:
    for lon, lat in tqdm(mesh_points):
        # Get elevation
        elev = get_elevation_at_point(lon, lat, dem)
        
        # Handle no-data points
        if elev < -1000 or elev > 10000 or np.isnan(elev):
            results.append({'lon': lon, 'lat': lat, 'status': 'NODATA'})
            nodata += 1
            continue
        
        # Check line of sight
        observer = wgs84.latlon(lat, lon, elevation_m=elev + 2)
        difference = satellite - observer
        topocentric = difference.at(ts.now())
        alt, az, distance = topocentric.altaz()
        
        if alt.degrees > 0:
            los = is_line_of_sight_clear(observer, (alt, az), dem)
            if los:
                results.append({'lon': lon, 'lat': lat, 'status': 'CLEAR', 'elev': elev})
                clear += 1
            else:
                results.append({'lon': lon, 'lat': lat, 'status': 'BLOCKED', 'elev': elev})
                blocked += 1
        else:
            results.append({'lon': lon, 'lat': lat, 'status': 'BELOW_HORIZON', 'elev': elev})

print(f"\n📊 RESULTS:")
print(f"  Clear: {clear} ({clear/len(mesh_points)*100:.1f}%)")
print(f"  Blocked: {blocked} ({blocked/len(mesh_points)*100:.1f}%)")
print(f"  No Data: {nodata} ({nodata/len(mesh_points)*100:.1f}%)")

# ASCII map
print(f"\n🗺️ VISIBILITY MAP:")
print("  □=Clear ■=Blocked ·=NoData")
for i in range(MESH_SIZE):
    print("  ", end="")
    for j in range(MESH_SIZE):
        status = results[i*MESH_SIZE + j]['status']
        if status == 'CLEAR': print("□", end=" ")
        elif status == 'BLOCKED': print("■", end=" ")
        else: print("·", end=" ")
    print()

print("\n✅ Complete! Now you should see blocked areas!")

100-POINT MESH ANALYSIS (FIXED)
Processing 100 points...


100%|██████████| 100/100 [00:16<00:00,  6.10it/s]


📊 RESULTS:
  Clear: 93 (93.0%)
  Blocked: 7 (7.0%)
  No Data: 0 (0.0%)

🗺️ VISIBILITY MAP:
  □=Clear ■=Blocked ·=NoData
  □ □ □ □ □ □ □ □ □ □ 
  □ □ □ □ □ □ □ □ □ □ 
  □ □ □ □ □ □ □ □ □ □ 
  □ □ □ □ □ ■ ■ □ □ □ 
  □ □ □ □ □ □ □ □ □ □ 
  □ □ ■ ■ □ □ □ □ □ □ 
  □ ■ □ □ □ □ □ □ □ □ 
  □ □ □ □ □ □ □ □ □ □ 
  □ □ □ □ □ □ □ □ □ □ 
  □ □ □ □ ■ ■ □ □ □ □ 

✅ Complete! Now you should see blocked areas!


In [13]:
# Cell 11: 5000-Point High-Resolution Mesh Analysis
import numpy as np
from tqdm import tqdm
import time

print("5000-POINT HIGH-RESOLUTION MESH ANALYSIS\n" + "="*40)

# Calculate grid size for ~5000 points
TOTAL_POINTS = 5000
MESH_SIZE = int(np.sqrt(TOTAL_POINTS))  # ~71x71 grid
ACTUAL_POINTS = MESH_SIZE * MESH_SIZE

print(f"📊 Configuration:")
print(f"  Target points: {TOTAL_POINTS}")
print(f"  Actual grid: {MESH_SIZE}×{MESH_SIZE} = {ACTUAL_POINTS} points")

# Generate mesh
lons = np.linspace(X_MIN, X_MAX, MESH_SIZE)
lats = np.linspace(Y_MIN, Y_MAX, MESH_SIZE)
lon_grid, lat_grid = np.meshgrid(lons, lats)
mesh_points = list(zip(lon_grid.ravel(), lat_grid.ravel()))

# Calculate spacing
lon_spacing_m = (X_MAX - X_MIN) * 111320 * np.cos(np.radians((Y_MIN + Y_MAX)/2)) / (MESH_SIZE - 1)
lat_spacing_m = (Y_MAX - Y_MIN) * 110540 / (MESH_SIZE - 1)
print(f"  Point spacing: ~{lon_spacing_m:.0f}m × {lat_spacing_m:.0f}m")

# Initialize results
results_5k = []
clear, blocked, nodata = 0, 0, 0

print(f"\n🔄 Processing {ACTUAL_POINTS} points...")
print("  (This will take a few minutes)")

start_time = time.time()

with rasterio.open(DEM_FILE_PATH) as dem:
    for lon, lat in tqdm(mesh_points, desc="Analyzing"):
        # Get elevation
        elev = get_elevation_at_point(lon, lat, dem)
        
        # Handle no-data
        if elev < -1000 or elev > 10000 or np.isnan(elev):
            results_5k.append({
                'lon': lon, 'lat': lat, 
                'status': 'NODATA', 'elev': -9999
            })
            nodata += 1
            continue
        
        # Check line of sight
        observer = wgs84.latlon(lat, lon, elevation_m=elev + 2)
        difference = satellite - observer
        topocentric = difference.at(ts.now())
        alt, az, distance = topocentric.altaz()
        
        if alt.degrees > 0:
            los = is_line_of_sight_clear(observer, (alt, az), dem)
            status = 'CLEAR' if los else 'BLOCKED'
            if los: clear += 1
            else: blocked += 1
        else:
            status = 'BELOW_HORIZON'
        
        results_5k.append({
            'lon': lon, 'lat': lat,
            'status': status, 'elev': elev,
            'sat_elevation': alt.degrees,
            'sat_azimuth': az.degrees
        })

elapsed = time.time() - start_time

print(f"\n✅ Processing complete!")
print(f"  Time: {elapsed:.1f} seconds ({elapsed/ACTUAL_POINTS*1000:.1f} ms/point)")

print(f"\n📊 RESULTS SUMMARY:")
print(f"  Total points: {ACTUAL_POINTS}")
print(f"  ✅ Clear: {clear} ({clear/ACTUAL_POINTS*100:.1f}%)")
print(f"  ❌ Blocked: {blocked} ({blocked/ACTUAL_POINTS*100:.1f}%)")
print(f"  ⚫ No Data: {nodata} ({nodata/ACTUAL_POINTS*100:.1f}%)")

# Create visibility matrix
vis_matrix_5k = np.zeros((MESH_SIZE, MESH_SIZE))
for i, r in enumerate(results_5k):
    row, col = i // MESH_SIZE, i % MESH_SIZE
    if r['status'] == 'CLEAR': vis_matrix_5k[row, col] = 1
    elif r['status'] == 'BLOCKED': vis_matrix_5k[row, col] = -1
    else: vis_matrix_5k[row, col] = 0

# Statistics
valid_elevs = [r['elev'] for r in results_5k if r['elev'] > -1000]
if valid_elevs:
    print(f"\n📏 ELEVATION STATS:")
    print(f"  Range: {np.min(valid_elevs):.1f}m to {np.max(valid_elevs):.1f}m")
    print(f"  Mean: {np.mean(valid_elevs):.1f}m")
    
    clear_elevs = [r['elev'] for r in results_5k if r['status'] == 'CLEAR']
    blocked_elevs = [r['elev'] for r in results_5k if r['status'] == 'BLOCKED']
    
    if clear_elevs:
        print(f"  Clear areas mean: {np.mean(clear_elevs):.1f}m")
    if blocked_elevs:
        print(f"  Blocked areas mean: {np.mean(blocked_elevs):.1f}m")

print(f"\n💾 Data saved to 'results_5k' ({len(results_5k)} points)")
print(f"   Ready for visualization!")

5000-POINT HIGH-RESOLUTION MESH ANALYSIS
📊 Configuration:
  Target points: 5000
  Actual grid: 70×70 = 4900 points
  Point spacing: ~72m × 116m

🔄 Processing 4900 points...
  (This will take a few minutes)


Analyzing: 100%|██████████| 4900/4900 [13:21<00:00,  6.11it/s]


✅ Processing complete!
  Time: 801.5 seconds (163.6 ms/point)

📊 RESULTS SUMMARY:
  Total points: 4900
  ✅ Clear: 4548 (92.8%)
  ❌ Blocked: 352 (7.2%)
  ⚫ No Data: 0 (0.0%)

📏 ELEVATION STATS:
  Range: 10.3m to 312.8m
  Mean: 133.4m
  Clear areas mean: 136.9m
  Blocked areas mean: 88.1m

💾 Data saved to 'results_5k' (4900 points)
   Ready for visualization!


In [15]:
# Cell 12: Create Interactive Folium Visualization for 5000 Points
import folium
from folium import plugins
import numpy as np

print("CREATING INTERACTIVE VISUALIZATION\n" + "="*40)

# Create base map
center_lat = (Y_MIN + Y_MAX) / 2
center_lon = (X_MIN + X_MAX) / 2

m = folium.Map(
    location=[center_lat, center_lon],
    zoom_start=14,
    tiles='OpenStreetMap'
)

# Add satellite imagery layer
folium.TileLayer(
    tiles='https://server.arcgisonline.com/ArcGIS/rest/services/World_Imagery/MapServer/tile/{z}/{y}/{x}',
    attr='Esri World Imagery',
    name='Satellite',
    overlay=False,
    control=True
).add_to(m)

print("📍 Adding visibility points...")

# Create feature groups
clear_group = folium.FeatureGroup(name='Clear LoS (Green)')
blocked_group = folium.FeatureGroup(name='Blocked LoS (Red)')
nodata_group = folium.FeatureGroup(name='No Data (Gray)')

# Add points with colors based on status
clear_points = []
blocked_points = []

for result in results_5k:
    lat, lon = result['lat'], result['lon']
    status = result['status']
    
    if status == 'CLEAR':
        clear_points.append([lat, lon])
        folium.CircleMarker(
            [lat, lon],
            radius=2,
            popup=f"Clear<br>Elev: {result['elev']:.1f}m<br>Sat: {result.get('sat_elevation', 0):.1f}°",
            color='green',
            fill=True,
            fillOpacity=0.7
        ).add_to(clear_group)
        
    elif status == 'BLOCKED':
        blocked_points.append([lat, lon])
        folium.CircleMarker(
            [lat, lon],
            radius=2,
            popup=f"Blocked<br>Elev: {result['elev']:.1f}m<br>Sat: {result.get('sat_elevation', 0):.1f}°",
            color='red',
            fill=True,
            fillOpacity=0.7
        ).add_to(blocked_group)
        
    elif status == 'NODATA':
        folium.CircleMarker(
            [lat, lon],
            radius=2,
            popup="No elevation data",
            color='gray',
            fill=True,
            fillOpacity=0.5
        ).add_to(nodata_group)

# Add groups to map
clear_group.add_to(m)
blocked_group.add_to(m)
nodata_group.add_to(m)

print(f"  Added {len(clear_points)} clear points")
print(f"  Added {len(blocked_points)} blocked points")

# Add heatmap layer for visibility
if clear_points:
    plugins.HeatMap(
        clear_points,
        name='Visibility Heatmap',
        min_opacity=0.3,
        radius=15,
        blur=10,
        gradient={0.4: 'blue', 0.65: 'lime', 1: 'green'}
    ).add_to(m)

# Add DEM boundary
folium.Rectangle(
    bounds=[[Y_MIN, X_MIN], [Y_MAX, X_MAX]],
    color='blue',
    weight=2,
    fill=False,
    popup='DEM Boundary'
).add_to(m)

# Add satellite position indicator
sat_az = np.mean([r.get('sat_azimuth', 0) for r in results_5k if 'sat_azimuth' in r])
sat_el = np.mean([r.get('sat_elevation', 0) for r in results_5k if 'sat_elevation' in r])

# Add legend
legend_html = f'''
<div style="position: fixed; 
     bottom: 50px; left: 50px; width: 250px; height: 140px; 
     background-color: white; z-index:9999; font-size:14px;
     border:2px solid grey; border-radius: 5px; padding: 10px">
     
     <b>GOES-17 Line-of-Sight Analysis</b><br>
     <span style="color:green;">●</span> Clear LoS: {clear} points<br>
     <span style="color:red;">●</span> Blocked: {blocked} points<br>
     <span style="color:gray;">●</span> No Data: {nodata} points<br>
     <hr>
     Satellite: Az={sat_az:.0f}°, El={sat_el:.0f}°<br>
     Total Points: {ACTUAL_POINTS}
</div>
'''
m.get_root().html.add_child(folium.Element(legend_html))

# Add layer control
folium.LayerControl().add_to(m)

# Save map
map_file = os.path.join(OUTPUT_DIR, 'woods_canyon_5000pt_visibility.html')
m.save(map_file)

print(f"\n✅ Map saved to: {map_file}")
print(f"   File size: {os.path.getsize(map_file)/1024/1024:.1f} MB")

# Create summary statistics map
print("\n📊 Creating summary visualization...")

# Calculate visibility percentage grid
grid_size = 10  # 10x10 summary grid
vis_percent = np.zeros((grid_size, grid_size))

for i in range(grid_size):
    for j in range(grid_size):
        # Get points in this cell
        lat_min = Y_MIN + i * (Y_MAX - Y_MIN) / grid_size
        lat_max = Y_MIN + (i + 1) * (Y_MAX - Y_MIN) / grid_size
        lon_min = X_MIN + j * (X_MAX - X_MIN) / grid_size
        lon_max = X_MIN + (j + 1) * (X_MAX - X_MIN) / grid_size
        
        cell_points = [r for r in results_5k 
                      if lat_min <= r['lat'] < lat_max 
                      and lon_min <= r['lon'] < lon_max
                      and r['status'] != 'NODATA']
        
        if cell_points:
            clear_count = sum(1 for r in cell_points if r['status'] == 'CLEAR')
            vis_percent[i, j] = (clear_count / len(cell_points)) * 100

# ASCII visualization
print("\nVISIBILITY PERCENTAGE MAP (% clear in each zone):")
print("  " + "-" * 41)
for row in vis_percent:
    print("  |", end="")
    for val in row:
        if val >= 75:
            print(" ██", end="")  # Mostly clear
        elif val >= 50:
            print(" ▓▓", end="")  # Mixed
        elif val >= 25:
            print(" ░░", end="")  # Mostly blocked
        else:
            print(" ··", end="")  # Blocked/No data
    print(" |")
print("  " + "-" * 41)
print("  Legend: ██=75-100% ▓▓=50-75% ░░=25-50% ··=0-25%")

print(f"\n🎉 VISUALIZATION COMPLETE!")
print(f"   Open {map_file} in your browser to explore")
print(f"   Use layer controls to toggle visibility groups")

# Display in notebook if available
try:
    display(m)
except:
    print("   (Map display not available in this environment)")

CREATING INTERACTIVE VISUALIZATION
📍 Adding visibility points...
  Added 4548 clear points
  Added 352 blocked points

✅ Map saved to: C:\Users\caleb\anaconda_projects\output\woods_canyon_5000pt_visibility.html
   File size: 5.2 MB

📊 Creating summary visualization...

VISIBILITY PERCENTAGE MAP (% clear in each zone):
  -----------------------------------------
  | ██ ██ ██ ██ ██ ██ ██ ██ ██ ██ |
  | ██ ██ ██ ░░ ██ ██ ██ ██ ██ ██ |
  | ██ ██ ██ ██ ██ ██ ██ ██ ██ ██ |
  | ██ ██ ██ ██ ██ ▓▓ ·· ░░ ██ ██ |
  | ██ ██ ██ ██ ██ ██ ██ ██ ██ ██ |
  | ██ ██ ▓▓ ██ ██ ██ ██ ██ ██ ██ |
  | ·· ██ ██ ██ ██ ██ ██ ██ ██ ██ |
  | ██ ██ ██ ██ ██ ██ ██ ██ ██ ██ |
  | ██ ██ ██ ██ ██ ██ ██ ██ ██ ██ |
  | ██ ▓▓ ▓▓ ██ ██ ██ ██ ██ ██ ██ |
  -----------------------------------------
  Legend: ██=75-100% ▓▓=50-75% ░░=25-50% ··=0-25%

🎉 VISUALIZATION COMPLETE!
   Open C:\Users\caleb\anaconda_projects\output\woods_canyon_5000pt_visibility.html in your browser to explore
   Use layer controls to toggle visibility g